In [1]:
import requests
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import json # library to handle JSON files
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    ca-certificates-2019.9.11  |       hecc5488_0         144 KB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    openssl-1.1.1c             |       h516909a_0         2.1 MB  conda-forge
    certifi-2019.9.11          |           py36_0         147 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

In [4]:
#Read the wiki page
website_url = requests.get('https://en.wikipedia.org/wiki/List_of_neighborhoods_in_Chicago').text
#Use BeautifulSoup
from bs4 import BeautifulSoup
soup = BeautifulSoup(website_url,'lxml')
#print(soup.prettify())
#Read  the table for 
My_table = soup.find('table',{'class':'wikitable sortable'})
#Read All the TR elements
tr_elements = My_table.findAll('tr')
tr_elements


[<tr>
 <th>Neighborhood</th>
 <th>Community area
 </th></tr>, <tr>
 <td>Albany Park
 </td>
 <td><a href="/wiki/Albany_Park,_Chicago" title="Albany Park, Chicago">Albany Park</a>
 </td></tr>, <tr>
 <td><a class="mw-redirect" href="/wiki/Altgeld_Gardens,_Chicago" title="Altgeld Gardens, Chicago">Altgeld Gardens</a>
 </td>
 <td>Riverdale
 </td></tr>, <tr>
 <td><a class="mw-redirect" href="/wiki/Andersonville,_Chicago" title="Andersonville, Chicago">Andersonville</a>
 </td>
 <td>Edgewater
 </td></tr>, <tr>
 <td>Archer Heights
 </td>
 <td><a href="/wiki/Archer_Heights,_Chicago" title="Archer Heights, Chicago">Archer Heights</a>
 </td></tr>, <tr>
 <td>Armour Square
 </td>
 <td><a href="/wiki/Armour_Square,_Chicago" title="Armour Square, Chicago">Armour Square</a>
 </td></tr>, <tr>
 <td>Ashburn
 </td>
 <td><a href="/wiki/Ashburn,_Chicago" title="Ashburn, Chicago">Ashburn</a>
 </td></tr>, <tr>
 <td>Ashburn Estates
 </td>
 <td>Ashburn
 </td></tr>, <tr>
 <td>Auburn Gresham
 </td>
 <td><a href="/

In [5]:
#get all the data in to table_contents
table_contents = []   # store your table here
for tr in tr_elements:
    if tr_elements.index(tr) == 0 : 
        row_cells = [ th.getText().strip() for th in tr.find_all('th') if th.getText().strip() != '' ]  
    else : 
        row_cells = ([ tr.find('th').getText() ] if tr.find('th') else [] ) + [ td.getText().strip() for td in tr.find_all('td') if td.getText().strip() != '' ] 
    if len(row_cells) > 1 : 
        table_contents += [ row_cells ]

table_contents

[['Neighborhood', 'Community area'],
 ['Albany Park', 'Albany Park'],
 ['Altgeld Gardens', 'Riverdale'],
 ['Andersonville', 'Edgewater'],
 ['Archer Heights', 'Archer Heights'],
 ['Armour Square', 'Armour Square'],
 ['Ashburn', 'Ashburn'],
 ['Ashburn Estates', 'Ashburn'],
 ['Auburn Gresham', 'Auburn Gresham'],
 ['Avalon Park', 'Avalon Park'],
 ['Avondale', 'Avondale'],
 ['Avondale Gardens', 'Irving Park'],
 ['Back of the Yards', 'New City'],
 ['Belmont Central', 'Belmont Cragin'],
 ['Belmont Gardens', 'Hermosa'],
 ['Belmont Heights', 'Dunning'],
 ['Belmont Terrace', 'Dunning'],
 ['Beverly', 'Beverly'],
 ['Beverly View', 'Ashburn'],
 ['Beverly Woods', 'Morgan Park'],
 ['Big Oaks', 'Norwood Park'],
 ['Boystown', 'Lake View'],
 ['Bowmanville', 'Lincoln Square'],
 ['Brainerd', 'Washington Heights'],
 ['Brickyard', 'Belmont Cragin'],
 ['Bridgeport', 'Bridgeport'],
 ['Brighton Park', 'Brighton Park'],
 ['Bronzeville', 'Douglas'],
 ['Bucktown', 'Logan Square'],
 ['Budlong Woods', 'Lincoln Squa

In [6]:
#Convert into Dataframe
df = pd.DataFrame(table_contents)
df.head()

0               1
0     Neighborhood  Community area
1      Albany Park     Albany Park
2  Altgeld Gardens       Riverdale
3    Andersonville       Edgewater
4   Archer Heights  Archer Heights

In [8]:
#Convert first row to row header
new_header = df.iloc[0] 
# take the rest of your data minus the header row
df = df[1:] 
# set the header row as the df header
df.columns = new_header 
# Lets see the 5 first rows of the new dataset
df.head()

0     Neighborhood  Community area
1      Albany Park     Albany Park
2  Altgeld Gardens       Riverdale
3    Andersonville       Edgewater
4   Archer Heights  Archer Heights
5    Armour Square   Armour Square

In [9]:
del df['Community area']
df.head()

0     Neighborhood
1      Albany Park
2  Altgeld Gardens
3    Andersonville
4   Archer Heights
5    Armour Square

In [10]:
df.shape

(246, 1)

In [11]:
#Get the Lat Long of Chicago
address = 'Chicago'

geolocator = Nominatim(user_agent="Chicago_explorer",timeout=3)
location = geolocator.geocode(address)
chi_latitude = location.latitude
chi_longitude = location.longitude
print('The geograpical coordinate of Chicago are {}, {}.'.format(chi_latitude, chi_longitude))

The geograpical coordinate of Chicago are 41.8755616, -87.6244212.


In [13]:
#get Lat and Long for the neighbourhoods and append to the dataframe
latitude = []
longitude = []
chi_area = []
for area in df['Neighborhood']:
  address = area + ", Chicago, Illinois, USA"  
  geolocator = Nominatim(user_agent="Chicago_explorer",timeout=10)
  location = geolocator.geocode(address)
  if location:
    latitude.append(location.latitude)
    longitude.append(location.longitude)
    chi_area.append(area)
    
chicago_df = pd.DataFrame({'Neighbour': chi_area, 'Latitude': latitude,'Longitude':longitude})
chicago_df.head(10)

Neighbour   Latitude  Longitude
0       Albany Park  41.971937 -87.716174
1   Altgeld Gardens  41.654864 -87.600446
2     Andersonville  41.977139 -87.669273
3    Archer Heights  41.811422 -87.726165
4     Armour Square  41.840033 -87.633107
5           Ashburn  41.747533 -87.711163
6    Auburn Gresham  41.743387 -87.656042
7       Avalon Park  41.745035 -87.588658
8          Avondale  41.938921 -87.711168
9  Avondale Gardens  41.938921 -87.711168

In [14]:
chicago_df.shape

(223, 3)

In [15]:
# Please refer the pdf for Folium map as not displayed in github
map_chicago = folium.Map(location=[chi_latitude, chi_longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(chicago_df['Latitude'], chicago_df['Longitude'], chicago_df['Neighbour']):
    label = '{}, {}'.format(neighborhood,'Chicago, Illinois, USA')
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#87cefa',
        fill_opacity=0.5,
        parse_html=False).add_to(map_chicago)

map_chicago

In [16]:
CLIENT_ID = 'TZW3OOD5YPYPAHK2GAGRFM44MKFP0NWGPNALMSKYNTQ30JET' # your Foursquare ID
CLIENT_SECRET = 'FLH0I3C5LH4JKOOAYQLBNOXWJMMWCD3LD5SVW1OTHIZECY1T' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 30
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: TZW3OOD5YPYPAHK2GAGRFM44MKFP0NWGPNALMSKYNTQ30JET
CLIENT_SECRET:FLH0I3C5LH4JKOOAYQLBNOXWJMMWCD3LD5SVW1OTHIZECY1T


In [35]:
chicago_df.loc[142, 'Neighbour']

"O'Hare"

In [36]:
#Get the neighborhood's latitude and longitude values.
neighborhood_latitude = chicago_df.loc[142, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = chicago_df.loc[142, 'Longitude'] # neighborhood longitude value
neighborhood_name = chicago_df.loc[142, 'Neighbour'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of O'Hare are 41.97310105, -87.9067678854723.


In [37]:
#Now, let's get the top 100 venues that are in Marble Hill within a radius of 500 meters.¶

radius = 500
LIMIT = 100
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, neighborhood_latitude, neighborhood_longitude, VERSION, radius, LIMIT)
url

'https://api.foursquare.com/v2/venues/explore?client_id=TZW3OOD5YPYPAHK2GAGRFM44MKFP0NWGPNALMSKYNTQ30JET&client_secret=FLH0I3C5LH4JKOOAYQLBNOXWJMMWCD3LD5SVW1OTHIZECY1T&ll=41.97310105,-87.9067678854723&v=20180604&radius=500&limit=100'

In [38]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5db1ed51598e64002c3dc0ab'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': '$-$$$$', 'key': 'price'}]},
  'headerLocation': 'Chicago',
  'headerFullLocation': 'Chicago',
  'headerLocationGranularity': 'city',
  'totalResults': 33,
  'suggestedBounds': {'ne': {'lat': 41.9776010545, 'lng': -87.90072639135015},
   'sw': {'lat': 41.968601045499994, 'lng': -87.91280937959446}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4e4d36b1b0fb57f6f227bf87',
       'name': 'Argo Tea',
       'location': {'address': 'Terminal 2, near Gate E3',
        'crossStreet': 'ORD Airport',
        'lat': 41.9753483785223,
        'lng': -87.90661359943748,
        'labeledLat

In [39]:
#From the Foursquare lab in the previous module, we know that all the information is in the items key. Before we proceed, let's borrow the get_category_type function from the Foursquare lab.
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [40]:
#Now we are ready to clean the json and structure it into a pandas dataframe.

venues = results['response']['groups'][0]['items']
nearby_venues = json_normalize(venues) # flatten JSON
# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]
# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)
# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]
nearby_venues.head()

name      categories        lat        lng
0       Argo Tea        Tea Room  41.975348 -87.906614
1    United Club  Airport Lounge  41.974562 -87.906666
2  Nuts On Clark     Snack Place  41.975664 -87.905963
3        Dunkin'      Donut Shop  41.975324 -87.906877
4       Argo Tea        Tea Room  41.975817 -87.902590

In [41]:
nearby_venues.shape

(33, 4)

In [42]:
nearby_venues

name           categories  \
0                                            Argo Tea             Tea Room   
1                                         United Club       Airport Lounge   
2                                       Nuts On Clark          Snack Place   
3                                             Dunkin'           Donut Shop   
4                                            Argo Tea             Tea Room   
5                                           Starbucks          Coffee Shop   
6                           Summer House Santa Monica  American Restaurant   
7                                    O'Hare Yoga Room          Yoga Studio   
8                                           Starbucks          Coffee Shop   
9                                 O'Hare URBAN Garden               Garden   
10                                      Auntie Anne's          Snack Place   
11                              Goose Island Beer Co.             Beer Bar   
12                                              Coach    Accessories Store   
13                        Wicker Park Seafood & Sushi     Sushi Restaurant   
14                                     Delta Sky Club       Airport Lounge   
15                                          Starbucks          Coffee Shop   
16                                         Brookstone    Electronics Store   
17                                  Uno Chicago Grill          Pizza Place   
18                                       Sunglass Hut    Accessories Store   
19                                          Starbucks          Coffee Shop   
20  Kids on the Fly, Chicago Children's Museum at ...           Playground   
21                                           HoyPoloi            Gift Shop   
22                                 Chicago O'Hare USO       Airport Lounge   
23                                      Auntie Anne's          Snack Place   
24                    American Airlines Admirals Club       Airport Lounge   
25                    Terminal 1 & 2 Corridor Gallery          Art Gallery   
26                               Butch O'Hare Exhibit        Historic Site   
27                                         Manchu Wok   Chinese Restaurant   
28                                           AA Eagle      Airport Service   
29                                             SUBWAY       Sandwich Place   
30                                   Cubs Bar & Grill                  Bar   
31                       Chicago O'Hare AE Break Room       Airport Lounge   
32                      Great American Bagel & Bakery           Bagel Shop   

          lat        lng  
0   41.975348 -87.906614  
1   41.974562 -87.906666  
2   41.975664 -87.905963  
3   41.975324 -87.906877  
4   41.975817 -87.902590  
5   41.973457 -87.903330  
6   41.976611 -87.905583  
7   41.975487 -87.903245  
8   41.976365 -87.905355  
9   41.975392 -87.903325  
10  41.975825 -87.905942  
11  41.977056 -87.907214  
12  41.976478 -87.906402  
13  41.976891 -87.906071  
14  41.974898 -87.906821  
15  41.974687 -87.908508  
16  41.974806 -87.905971  
17  41.974719 -87.908796  
18  41.974854 -87.906154  
19  41.975859 -87.902440  
20  41.976031 -87.904785  
21  41.977193 -87.907092  
22  41.976162 -87.904634  
23  41.974482 -87.903260  
24  41.974149 -87.903029  
25  41.977281 -87.906457  
26  41.977131 -87.906501  
27  41.975694 -87.903426  
28  41.973338 -87.903236  
29  41.975669 -87.902986  
30  41.975581 -87.902997  
31  41.974893 -87.903348  
32  41.975589 -87.902928

In [44]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [48]:
chicago_venues = getNearbyVenues(names=chicago_df['Neighbour'],
                                   latitudes=chicago_df['Latitude'],
                                   longitudes=chicago_df['Longitude']
                                  )

Albany Park
Altgeld Gardens
Andersonville
Archer Heights
Armour Square
Ashburn
Auburn Gresham
Avalon Park
Avondale
Avondale Gardens
Back of the Yards
Belmont Central
Belmont Gardens
Belmont Terrace
Beverly
Beverly View
Beverly Woods
Big Oaks
Boystown
Bowmanville
Brainerd
Brickyard
Bridgeport
Brighton Park
Bronzeville
Bucktown
Budlong Woods
Buena Park
Burnside
Cabrini–Green
Calumet Heights
Canaryville
Central Station
Chatham
Chicago Lawn
Chinatown
Chrysler Village
Clarendon Park
Clearing East
Clearing West
Cragin
Crestline
Dearborn Homes
Dearborn Park
Douglas Park
Dunning
East Beverly
East Chatham
East Garfield Park
East Hyde Park
East Pilsen
East Side
East Village
Eden Green
Edgebrook
Edgewater
Edgewater Beach
Edgewater Glen
Edison Park
Englewood
Fernwood
Fifth City
Ford City
Forest Glen
Fuller Park
Gage Park
Galewood
The Gap
Garfield Ridge
Gladstone Park
Gold Coast
Golden Gate
Goose Island
Graceland West
Grand Boulevard
Grand Crossing
Greater Grand Crossing
Greektown
Gresham
Groveland

In [49]:
print(chicago_venues.shape)
chicago_venues.head()

(5785, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Albany Park              41.971937              -87.716174   
1  Albany Park              41.971937              -87.716174   
2  Albany Park              41.971937              -87.716174   
3  Albany Park              41.971937              -87.716174   
4  Albany Park              41.971937              -87.716174   

                        Venue  Venue Latitude  Venue Longitude  \
0  Cairo Nights Hookah Lounge       41.975776       -87.715547   
1             Chicago Produce       41.970553       -87.716327   
2                   Nighthawk       41.967974       -87.713415   
3                   Banpojung       41.975707       -87.715609   
4   Popeyes Louisiana Kitchen       41.968459       -87.713156   

        Venue Category  
0           Hookah Bar  
1        Grocery Store  
2         Cocktail Bar  
3    Korean Restaurant  
4  Fried Chicken Joint

In [50]:
chicago_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                              
Albany Park                                          13   
Altgeld Gardens                                       1   
Andersonville                                        79   
Archer Heights                                       20   
Armour Square                                        11   
Ashburn                                               4   
Auburn Gresham                                        4   
Avalon Park                                          15   
Avondale                                             30   
Avondale Gardens                                     30   
Back of the Yards                                    32   
Belmont Central                                      66   
Belmont Gardens                                      66   
Belmont Terrace                                      66   
Beverly                                              12   
Beverly View                                         12   
Beverly Woods                                         9   
Big Oaks                                              2   
Bowmanville                                          27   
Boystown                                            100   
Brainerd                                              8   
Brickyard                                            43   
Bridgeport                                           37   
Brighton Park                                        18   
Bronzeville                                          18   
Bucktown                                            100   
Budlong Woods                                        21   
Buena Park                                           50   
Burnside                                              4   
Cabrini–Green                                        33   
Calumet Heights                                       5   
Canaryville                                          10   
Central Station                                      13   
Chatham                                               6   
Chicago Lawn                                         12   
Chinatown                                            48   
Chrysler Village                                      5   
Clarendon Park                                       37   
Clearing East                                        14   
Clearing West                                        14   
Cragin                                               15   
Crestline                                             6   
Dearborn Homes                                        7   
Dearborn Park                                        89   
Douglas Park                                          6   
Dunning                                               4   
East Beverly                                         12   
East Chatham                                          6   
East Garfield Park                                   10   
East Hyde Park                                       26   
East Pilsen                                          60   
East Side                                             9   
East Village                                         29   
Eden Green                                           16   
Edgebrook                                            22   
Edgewater                                            56   
Edgewater Beach                                      56   
Edgewater Glen                                       37   
Edison Park                                          26   
Englewood                                            17   
Fernwood                                              8   
Fifth City                                            5   
Ford City                                            37   
Forest Glen                                           7   
Fuller Park                                           6   
Gage Park                                             9   
Galewood              

In [51]:
print('There are {} uniques categories.'.format(len(chicago_venues['Venue Category'].unique())))

There are 333 uniques categories.


In [52]:
#Analyze Each Neighborhood
# one hot encoding
chicago_onehot = pd.get_dummies(chicago_venues[['Venue Category']], prefix="", prefix_sep="")
# add neighborhood column back to dataframe
chicago_onehot['Neighborhood'] = chicago_venues['Neighborhood'] 
# move neighborhood column to the first column
fixed_columns = [chicago_onehot.columns[-1]] + list(chicago_onehot.columns[:-1])
chicago_onehot = chicago_onehot[fixed_columns]
chicago_onehot.head()

Neighborhood  ATM  Accessories Store  Adult Boutique  African Restaurant  \
0  Albany Park    0                  0               0                   0   
1  Albany Park    0                  0               0                   0   
2  Albany Park    0                  0               0                   0   
3  Albany Park    0                  0               0                   0   
4  Albany Park    0                  0               0                   0   

   Airport  Airport Food Court  Airport Lounge  Airport Service  \
0        0                   0               0                0   
1        0                   0               0                0   
2        0                   0               0                0   
3        0                   0               0                0   
4        0                   0               0                0   

   Airport Terminal  Alternative Healer  American Restaurant  Antique Shop  \
0                 0                   0                    0             0   
1                 0                   0                    0             0   
2                 0                   0                    0             0   
3                 0                   0                    0             0   
4                 0                   0                    0             0   

   Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0       0                 0                       0            0           0   
1       0                 0                       0            0           0   
2       0                 0                       0            0           0   
3       0                 0                       0            0           0   
4       0                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Dealership  \
0                    0                 0                   0                0   
1                    0                 0                   0                0   
2                    0                 0                   0                0   
3                    0                 0                   0                0   
4                    0                 0                   0                0   

   Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0                0          0           0           0       0     0    0   
1                0          0           0           0       0     0    0   
2                0          0           0           0       0     0    0   
3                0          0           0           0       0     0    0   
4                0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Beach  Bed & Breakfast  \
0               0                 0                 0      0                0   
1               0                 0                 0      0                0   
2               0                 0                 0      0                0   
3               0                 0                 0      0                0   
4               0                 0                 0      0                0   

   Beer Bar  Beer Garden  Beer Store  Big Box Store  Bike Rental / Bike Share  \
0         0            0           0              0                         0   
1         0            0           0              0                         0   
2         0            0           0              0                         0   
3         0            0           0              0                         0   
4         0            0           0              0                         0   

   Bike Shop  Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0          0       0           0              0          0         0   
1          0       0           0              0          0         0   
2          0       0           0              

In [53]:
chicago_onehot.shape

(5785, 334)

In [54]:
#Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

chicago_grouped = chicago_onehot.groupby('Neighborhood').mean().reset_index()
chicago_grouped

Neighborhood       ATM  Accessories Store  \
0                         Albany Park  0.000000           0.000000   
1                     Altgeld Gardens  0.000000           0.000000   
2                       Andersonville  0.000000           0.000000   
3                      Archer Heights  0.000000           0.000000   
4                       Armour Square  0.000000           0.000000   
5                             Ashburn  0.000000           0.000000   
6                      Auburn Gresham  0.000000           0.000000   
7                         Avalon Park  0.066667           0.000000   
8                            Avondale  0.000000           0.000000   
9                    Avondale Gardens  0.000000           0.000000   
10                  Back of the Yards  0.000000           0.000000   
11                    Belmont Central  0.000000           0.000000   
12                    Belmont Gardens  0.000000           0.000000   
13                    Belmont Terrace  0.000000           0.000000   
14                            Beverly  0.000000           0.000000   
15                       Beverly View  0.000000           0.000000   
16                      Beverly Woods  0.000000           0.000000   
17                           Big Oaks  0.000000           0.000000   
18                        Bowmanville  0.000000           0.000000   
19                           Boystown  0.000000           0.000000   
20                           Brainerd  0.000000           0.000000   
21                          Brickyard  0.000000           0.023256   
22                         Bridgeport  0.000000           0.000000   
23                      Brighton Park  0.000000           0.000000   
24                        Bronzeville  0.000000           0.000000   
25                           Bucktown  0.000000           0.020000   
26                      Budlong Woods  0.000000           0.000000   
27                         Buena Park  0.000000           0.000000   
28                           Burnside  0.000000           0.000000   
29                      Cabrini–Green  0.000000           0.000000   
30                    Calumet Heights  0.000000           0.000000   
31                        Canaryville  0.000000           0.000000   
32                    Central Station  0.000000           0.000000   
33                            Chatham  0.000000           0.000000   
34                       Chicago Lawn  0.000000           0.000000   
35                          Chinatown  0.000000           0.000000   
36                   Chrysler Village  0.000000           0.000000   
37                     Clarendon Park  0.000000           0.000000   
38                      Clearing East  0.000000           0.000000   
39                      Clearing West  0.000000           0.000000   
40                             Cragin  0.000000           0.000000   
41                          Crestline  0.000000           0.000000   
42                     Dearborn Homes  0.000000           0.000000   
43                      Dearborn Park  0.000000           0.000000   
44                       Douglas Park  0.000000           0.000000   
45                            Dunning  0.000000           0.000000   
46                       East Beverly  0.000000           0.000000   
47                       East Chatham  0.000000           0.000000   
48                 East Garfield Park  0.000000           0.000000   
49                     East Hyde Park  0.000000           0.000000   
50                        East Pilsen  0.000000           0.000000   
51                          East Side  0.000000           0.000000   
52                       East Village  0.000000           0.000000   
53                         Eden Green  0.000000           0.000000   
54                          Edgebrook  0.000000           0.000000   
55                          Edgewater  0.000000           0.000000   
56                    Edgewater Bea

In [55]:
#Let's print each neighborhood along with the top 5 most common venues

num_top_venues = 5
for hood in chicago_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = chicago_grouped[chicago_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Albany Park----
               venue  freq
0     Sandwich Place  0.15
1  Korean Restaurant  0.08
2       Cocktail Bar  0.08
3             Bakery  0.08
4  Mobile Phone Shop  0.08


----Altgeld Gardens----
                     venue  freq
0                     Park   1.0
1                      ATM   0.0
2  New American Restaurant   0.0
3        Outdoor Sculpture   0.0
4             Optical Shop   0.0


----Andersonville----
                venue  freq
0         Coffee Shop  0.04
1      Sandwich Place  0.04
2  Italian Restaurant  0.04
3           Pet Store  0.03
4           Gift Shop  0.03


----Archer Heights----
                  venue  freq
0     Mobile Phone Shop  0.15
1         Grocery Store  0.10
2           Gas Station  0.10
3    Seafood Restaurant  0.05
4  Gym / Fitness Center  0.05


----Armour Square----
                venue  freq
0  Chinese Restaurant  0.27
1          Sports Bar  0.09
2       Hot Dog Joint  0.09
3         Gas Station  0.09
4      Sandwich Place  0.09


---

In [87]:
#Let's put that into a pandas dataframe
#First, let's write a function to sort the venues in descending order.

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

#Now let's create the new dataframe and display the top 10 venues for each neighborhood.

num_top_venues = 5
indicators = ['st', 'nd', 'rd']
# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = chicago_grouped['Neighborhood']

for ind in np.arange(chicago_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(chicago_grouped.iloc[ind, :], num_top_venues) 

neighborhoods_venues_sorted


Neighborhood            1st Most Common Venue  \
0                         Albany Park                   Sandwich Place   
1                     Altgeld Gardens                             Park   
2                       Andersonville                      Coffee Shop   
3                      Archer Heights                Mobile Phone Shop   
4                       Armour Square               Chinese Restaurant   
5                             Ashburn                  Automotive Shop   
6                      Auburn Gresham                 Basketball Court   
7                         Avalon Park                         Boutique   
8                            Avondale                    Grocery Store   
9                    Avondale Gardens                    Grocery Store   
10                  Back of the Yards               Mexican Restaurant   
11                    Belmont Central              Japanese Restaurant   
12                    Belmont Gardens              Japanese Restaurant   
13                    Belmont Terrace              Japanese Restaurant   
14                            Beverly                   Cosmetics Shop   
15                       Beverly View                   Cosmetics Shop   
16                      Beverly Woods                       Playground   
17                           Big Oaks       Construction & Landscaping   
18                        Bowmanville      Eastern European Restaurant   
19                           Boystown                          Gay Bar   
20                           Brainerd                   Discount Store   
21                          Brickyard                       Shoe Store   
22                         Bridgeport                             Park   
23                      Brighton Park               Mexican Restaurant   
24                        Bronzeville                     Liquor Store   
25                           Bucktown                      Pizza Place   
26                      Budlong Woods                           Bakery   
27                         Buena Park                      Coffee Shop   
28                           Burnside                     Intersection   
29                      Cabrini–Green                           Lounge   
30                    Calumet Heights                      Bus Station   
31                        Canaryville                      Pizza Place   
32                    Central Station                             Park   
33                            Chatham                             Park   
34                       Chicago Lawn                      Pizza Place   
35                          Chinatown               Chinese Restaurant   
36                   Chrysler Village               Mexican Restaurant   
37                     Clarendon Park                             Park   
38                      Clearing East                      Pizza Place   
39                      Clearing West                      Pizza Place   
40                             Cragin               Mexican Restaurant   
41                          Crestline                       Donut Shop   
42                     Dearborn Homes               Chinese Restaurant   
43                      Dearborn Park                   Sandwich Place   
44                       Douglas Park                             Café   
45                            Dunning                    Deli / Bodega   
46                       East Beverly                   Cosmetics Shop   
47                       East Chatham                             Park   
48                 East Garfield Park                         Pharmacy   
49                     East Hyde Park                      Coffee Shop   
50                        East Pilsen               Mexican Restaurant   
51                          East Side                      Pizza Place   
52                       East Village                   Sandwich Place   
53                         Ed

In [88]:
#Cluster Neighborhoods
#Run k-means to cluster the neighborhood into 5 clusters.

# set number of clusters
kclusters = 5

chicago_grouped_clustering = chicago_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(chicago_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_



array([1, 4, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 1, 0, 1, 0, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1,
       1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1,
       1, 1, 1, 1, 4, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 0, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 2, 1, 1, 1,
       1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1,
       1, 1, 0, 1, 0, 0, 1, 4, 1, 1, 4, 0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0,
       4, 1, 1, 3, 1, 1, 1, 1, 1, 1, 1, 0, 2, 1, 0, 1, 1, 1, 1, 2, 1, 0,
       1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1,
       1, 1, 0, 1, 1, 1, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 0, 0, 1, 1],
      dtype=int32)

In [94]:
#Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
# add clustering labels

#neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
chicago_merged = chicago_df.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighbour')
#chicago_merged # check the last columns!
print(chicago_merged.shape)
chicago_merged = chicago_merged[np.isfinite(chicago_merged['Cluster Labels'])]
print(chicago_merged.shape)


(223, 9)
(220, 9)


In [97]:
# create map
map_clusters = folium.Map(location=[41.8755616, -87.6244212], zoom_start=11)    #   [latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(chicago_merged['Latitude'], chicago_merged['Longitude'], chicago_merged['Neighbour'], chicago_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)

    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
    
map_clusters

In [86]:
chicago_merged.head()

Neighbour   Latitude  Longitude  Cluster Labels  \
0      Albany Park  41.971937 -87.716174             0.0   
1  Altgeld Gardens  41.654864 -87.600446             3.0   
2    Andersonville  41.977139 -87.669273             0.0   
3   Archer Heights  41.811422 -87.726165             0.0   
4    Armour Square  41.840033 -87.633107             0.0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Sandwich Place     Korean Restaurant          Cocktail Bar   
1                  Park           Yoga Studio           Fabric Shop   
2           Coffee Shop        Sandwich Place    Italian Restaurant   
3     Mobile Phone Shop           Gas Station         Grocery Store   
4    Chinese Restaurant        Cosmetics Shop         Hot Dog Joint   

         4th Most Common Venue 5th Most Common Venue  6th Most Common Venue  \
0            Mobile Phone Shop                 Diner          Grocery Store   
1  Eastern European Restaurant     Electronics Store  Entertainment Service   
2         Gym / Fitness Center              Beer Bar              Pet Store   
3         Gym / Fitness Center         Big Box Store         Sandwich Place   
4               Sandwich Place        Breakfast Spot             Sports Bar   

  7th Most Common Venue      8th Most Common Venue 9th Most Common Venue  \
0    Chinese Restaurant        Fried Chicken Joint            Donut Shop   
1  Ethiopian Restaurant                Event Space               Exhibit   
2           Pizza Place  Middle Eastern Restaurant                Lounge   
3    Mexican Restaurant               Optical Shop    Seafood Restaurant   
4      Asian Restaurant                Gas Station    Italian Restaurant   

  10th Most Common Venue  
0                 Bakery  
1             Eye Doctor  
2     Salon / Barbershop  
3     Italian Restaurant  
4                Exhibit